In [2]:
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib as mpl

# 300, 900, 1800, 7200, 14400, 86400
param = ['USDT_ETH', '1488326400', '9999999999', '1800']
URL = 'https://poloniex.com/public?command=returnChartData&currencyPair={}&start={}&end={}&period={}'.format(*param)
chart = pd.read_json(URL)


In [41]:
chart['ema12'] = chart['close'].ewm(span=12,min_periods=0,adjust=True,ignore_na=False).mean()
chart['ema26'] = chart['close'].ewm(span=26,min_periods=0,adjust=True,ignore_na=False).mean()
chart['macd'] = chart['ema12'] - chart['ema26']
chart['signal'] = chart['macd'].ewm(span=9,min_periods=0,adjust=True,ignore_na=False).mean()
chart['diff'] = chart['macd'] - chart['signal']

# SMA
chart['sma50'] = chart['close'].rolling(window=50,center=False).mean()
chart['sma40'] = chart['close'].rolling(window=40,center=False).mean()
chart['sma30'] = chart['close'].rolling(window=30,center=False).mean()

# EMA
chart['ema40'] = chart['close'].ewm(span=30,min_periods=0,adjust=True,ignore_na=False).mean()
chart['ema30'] = chart['close'].ewm(span=30,min_periods=0,adjust=True,ignore_na=False).mean()
chart['ema20'] = chart['close'].ewm(span=20,min_periods=0,adjust=True,ignore_na=False).mean()


# chart['diff'] = chart['sma50'] - chart['sma50'].shift(1)
# chart['change'] = (chart['sma50'] / chart['sma50'].shift(1)) -1

# chart.head()
chart.head()

close                date       high        low      open  quoteVolume  \
0  15.800000 2017-03-01 00:00:00  15.800000  15.620000  15.62200    21.810836   
1  15.708536 2017-03-01 00:30:00  15.800000  15.572002  15.80000   532.343595   
2  15.600344 2017-03-01 01:00:00  15.750000  15.600004  15.71062    82.832956   
3  15.670000 2017-03-01 01:30:00  15.799956  15.620000  15.69000   303.295708   
4  15.789800 2017-03-01 02:00:00  15.799951  15.670000  15.68000    72.168197   

        volume  weightedAverage      ema12      ema26      macd    signal  \
0   344.401627        15.790391  15.800000  15.800000  0.000000  0.000000   
1  8362.134460        15.708153  15.750457  15.752509 -0.002052 -0.001140   
2  1297.119036        15.659456  15.691868  15.697838 -0.005970 -0.003119   
3  4748.317083        15.655734  15.684965  15.690055 -0.005090 -0.003787   
4  1136.578089        15.749016  15.713448  15.713187  0.000262 -0.002583   

       diff  sma50  sma40  sma30      ema40      ema30      ema20  
0  0.000000    NaN    NaN    NaN  15.800000  15.800000  15.800000  
1 -0.000912    NaN    NaN    NaN  15.752743  15.752743  15.751981  
2 -0.002850    NaN    NaN    NaN  15.698521  15.698521  15.696301  
3 -0.001303    NaN    NaN    NaN  15.690662  15.690662  15.688708  
4  0.002844    NaN    NaN    NaN  15.713218  15.713218  15.713161

In [3]:
%matplotlib inline
# pd.set_option('display.mpl_style', 'default')

plt.rcParams['figure.figsize'] = (20, 10)

# plt.plot(chart['macd'])
# plt.plot(chart['signal'])
# plt.plot(chart['diff'])


# plt.plot(chart['sma50'], '.')
# plt.plot(chart['ema30'], '.')
# plt.plot(chart['weightedAverage'], '.')


plt.plot(chart['sma40'])
plt.plot(chart['ema30'])

plt.plot(chart['sma30'])
plt.plot(chart['ema20'])

plt.plot(chart['macd'])
plt.plot(chart['signal'])


plt.show()

# chart['change'].plot(figsize=(15, 10))

In [16]:
size = chart.date.count()
factor = 1.01

result = [[] for x in range(7)]

for i in range(size):
    buy = chart.iloc[i]
    sellPrice = buy.weightedAverage * factor
    
    for y in range(i+1, min(i+335, size)):
        if chart.iloc[y].weightedAverage > sellPrice:
            count = int((y-i)/48)
            result[count].append(buy)
            break
                
                

In [18]:
count = 0
for item in result:
    # print(len(item))
    count += len(item)
count


28048

In [17]:
for i in result:
    print(len(i))

22976
2465
975
641
466
247
278


In [38]:
result

[[close                             15.8
  date               2017-03-01 00:00:00
  high                              15.8
  low                              15.62
  open                            15.622
  quoteVolume                    21.8108
  volume                         344.402
  weightedAverage                15.7904
  ema12                             15.8
  ema26                             15.8
  macd                                 0
  signal                               0
  diff                                 0
  sma50                              NaN
  sma40                              NaN
  sma30                              NaN
  ema40                             15.8
  ema30                             15.8
  ema20                             15.8
  Name: 0, dtype: object, close                          15.7085
  date               2017-03-01 00:30:00
  high                              15.8
  low                             15.572
  open                           

In [40]:
day1 = pd.DataFrame(result[0])
day1['trend'] = day1['ema20'] - day1['sma30']


a = [x for x in range(-10, 11, 1)]
b = [(x/10) for x in range(-10, 11, 1)]

plt.hist(day1['trend'], a)
plt.show()